In [1]:
import pandas as pd
import torch
from torch.autograd import Variable
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import collections
import operator

In [3]:
train = pd.read_csv("cleaned_train.csv")

In [5]:
test = pd.read_csv("cleaned_test.csv")

In [6]:
train

PRODUCT_ID  \
1925202  ArtzFolio Tulip Flowers Blackout Curtain for D...   
2673191  Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2765088  PRIKNIK Horn Red Electric Air Horn Compressor ...   
1594019  ALISHAH Women's Cotton Ankle Length Leggings C...   
283658   The United Empire Loyalists: A Chronicle of th...   
...                                                    ...   
2422167  Nike Women's As W Ny Df Swsh Hn Kh Bra (CZ7610...   
2766635  (3PCS) Goose Game Cute Cartoon Enamel Pins, Fu...   
1987786  Kangroo Sweep Movement Printed Wooden Wall Clo...   
1165754  Electro Voice EKX-BRKT15 | Wall Mount Bracket ...   
1072666  Skyjacker C7360SP Component Box For PN[C7360PK...   

                                                     TITLE  \
1925202  LUXURIOUS & APPEALING: Beautiful custom-made c...   
2673191  Harry Potter Hedwig Pyjamas (6-16 Yrs) 100% co...   
2765088  Loud Dual Tone Trumpet Horn  Compatible With S...   
1594019  Made By 95%cotton and 5% Lycra which gives you...   
283658                                                 NaN   
...                                                    ...   
2422167                                 aterial : Polyeste   
2766635  ❤ [Inspiration] Inspired by the Untitled Goose...   
1987786  Dial size: 12 inches in diameter Big  clear re...   
1165754                                                NaN   
1072666  Component Box For PN[C7360PK] 4 in. Lift Incl....   

                                             BULLET_POINTS  DESCRIPTION  \
1925202                                                NaN         1650   
2673191                                                NaN         2755   
2765088  Specifications: Color: Red, Material: Aluminiu...         7537   
1594019  AISHAH Women's Lycra Cotton Ankel Leggings. Br...         2996   
283658                                                 NaN         6112   
...                                                    ...          ...   
2422167                                                NaN         3009   
2766635  <p><b>[Brand]: </b>XVIEONR</p> <p><br></p> <p>...         3413   
1987786  Wall Clocks Are Very Attractive In Looks And E...         1574   
1165754                                                NaN          592   
1072666  Skyjacker C7360SP Component Box For PN[C7360PK...         7367   

         PRODUCT_TYPE_ID                                     PRODUCT_LENGTH  
1925202      2125.980000  artzfolio tulip flowers blackout curtain door ...  
2673191       393.700000  marks spencer girls' pyjama sets t862561cnavy ...  
2765088       748.031495  priknik horn red electric air horn compressor ...  
1594019       787.401574  alishah women's cotton ankle length leggings c...  
283658        598.424000  united empire loyalists chronicle great migration  
...                  ...                                                ...  
2422167      1181.100000  nike women's w ny df swsh hn kh bra cz7610010b...  
2766635       125.984252  3pcs goose game cute cartoon enamel pins funny...  
1987786      1200.000000  kangroo sweep movement printed wooden wall clo...  
1165754      2900.000000  electro voice ekxbrkt15 wall mount bracket ekx...  
1072666      2000.000000  skyjacker c7360sp component box pnc7360pk 4 li...  

[2249698 rows x 6 columns]

In [216]:
small_train = train.iloc[1:100]
small_test = test.iloc[0:1000]

In [176]:
small_train

PRODUCT_ID  \
2673191  Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2765088  PRIKNIK Horn Red Electric Air Horn Compressor ...   
1594019  ALISHAH Women's Cotton Ankle Length Leggings C...   
283658   The United Empire Loyalists: A Chronicle of th...   
2152929  HINS Metal Bucket Shape Plant Pot for Indoor &...   
...                                                    ...   
1257943   Soffe Girls' Big Core Tank Top, Surf Blue, Small   
162117   The Governance and Regulation of International...   
163240   The Interfaith Alternative: Embracing Spiritua...   
1428724                                     Midnight Rider   
1479974  Muellery Recycling Bag Recycle Box Bins Waterp...   

                                                     TITLE  \
2673191  Harry Potter Hedwig Pyjamas (6-16 Yrs) 100% co...   
2765088  Loud Dual Tone Trumpet Horn  Compatible With S...   
1594019  Made By 95%cotton and 5% Lycra which gives you...   
283658                                                 NaN   
2152929  Simple and elegant  great for displaying indoo...   
...                                                    ...   
1257943  Great fit High neckline Tank top Slim Fit Grea...   
162117                                                 NaN   
163240                                                 NaN   
1428724                                                NaN   
1479974  Set of 3 bags for sorting and recycling waste....   

                                             BULLET_POINTS  DESCRIPTION  \
2673191                                                NaN         2755   
2765088  Specifications: Color: Red, Material: Aluminiu...         7537   
1594019  AISHAH Women's Lycra Cotton Ankel Leggings. Br...         2996   
283658                                                 NaN         6112   
2152929  HINS Brings you the most Elegant Looking Pot w...         5725   
...                                                    ...          ...   
1257943                                                NaN         2779   
162117                                                 NaN          123   
163240                                                 NaN          139   
1428724                                                NaN            7   
1479974                                                NaN         8501   

         PRODUCT_TYPE_ID                                     PRODUCT_LENGTH  
2673191       393.700000  marks spencer girls' pyjama sets t862561cnavy ...  
2765088       748.031495  priknik horn red electric air horn compressor ...  
1594019       787.401574  alishah women's cotton ankle length leggings c...  
283658        598.424000  united empire loyalists chronicle great migration  
2152929       950.000000  hins metal bucket shape plant pot indoor outdo...  
...                  ...                                                ...  
1257943      1130.000000  soffe girls' big core tank top surf blue small...  
162117        600.000000  governance regulation international finance pr...  
163240        550.000000  interfaith alternative embracing spiritual div...  
1428724       550.000000                                     midnight rider  
1479974      1591.000000  muellery recycling bag recycle box bins waterp...  

[99999 rows x 6 columns]

In [152]:
small_test

PRODUCT_ID  \
604373   Manuel d'Héliogravure Et de Photogravure En Re...   
1729783  DCGARING Microfiber Throw Blanket Warm Fuzzy P...   
1871949  I-Match Auto Parts Front License Plate Bracket...   
1107571  PinMart Gold Plated Excellence in Service 1 Ye...   
624253   Visual Mathematics, Illustrated by the TI-92 a...   
...                                                    ...   
2825486  ZUVINO Stylish Top for Women | Latest Summer C...   
387912   Help! My Students Are Driving Me Crazy: An Eas...   
2373559  Lappy Hub Keyboard Compatible for VAIO PCG-718...   
2739688  NG CREATION Hard Beans Wax For Unwanted Hair R...   
2092925  SURITCH for Pixel 4a 5G Case 6.2 inch (2020), ...   

                                                     TITLE  \
604373                                                 NaN   
1729783  QUALITY GUARANTEED: Luxury cozy plush polyeste...   
1871949  Front License Plate Bracket Made Of Plastic Di...   
1107571  Available as a single item or bulk packed. Sel...   
624253                                                 NaN   
...                                                    ...   
2825486  Latest Stylish Western Wear Top For Women || T...   
387912                                                 NaN   
2373559  Genuine quality product Tested before shipping...   
2739688  Whether You Need To Remove Fine Or Rough Hair ...   
2092925  【For 5G Verizon ONLY】: This Pixel 4a protectiv...   

                                             BULLET_POINTS  DESCRIPTION  \
604373                                                 NaN         6142   
1729783  <b>DCGARING Throw Blanket</b><br><br> <b>Size ...         1622   
1871949  Replacement for The Following Vehicles:2020 LE...         7540   
1107571  Our Excellence in Service Lapel Pins feature a...        12442   
624253                                                 NaN         6318   
...                                                    ...          ...   
2825486  ZUVINO brings to you latest stylish western we...         3077   
387912                                                 NaN          123   
2373559  Lappy Hub Keyboard Compatible for VAIO PCG-718...         6888   
2739688  Whether You Need To Remove Fine Or Rough Hair,...        13051   
2092925  <p>Play up your best style, SURITCH bring pass...        12556   

                                           PRODUCT_TYPE_ID  
604373   manuel d'hliogravure et de photogravure en rel...  
1729783  dcgaring microfiber throw blanket warm fuzzy p...  
1871949  imatch auto parts front license plate bracket ...  
1107571  pinmart gold plated excellence service 1 year ...  
624253            visual mathematics illustrated ti92 ti89  
...                                                    ...  
2825486  zuvino stylish top women latest summer cotton ...  
387912   help students driving crazy easy guide classro...  
2373559  lappy hub keyboard compatible vaio pcg71811l p...  
2739688  ng creation hard beans wax unwanted hair remov...  
2092925  suritch pixel 4a 5g case 62 inch 2020 built sc...  

[1000 rows x 5 columns]

In [213]:
shit_words = "the of to and a in is it you that he was for on are with as I his they be at one have this from or had by not word but what some we can out other were all there when up use your how said an each she which do their time if will way about many then them write would like so these her long make thing see him two has look more day could go come did number sound no most people my over know water than call first who may down side been now find any new work part take get place made live where after back little only round man year came show every good me give our under name very through just form sentence great think say help low line differ turn cause much mean before move right boy old too same tell does set three want air well also play small end put home read hand port large spell add even land here must big high such follow act why ask men change went light kind off need house picture try us again animal point mother world near build self earth father head stand own page should country found answer school grow study still learn plant cover food sun four between state keep eye never last let thought city tree cross farm hard start might story saw far sea draw left late run don't while press close night real life few north open seem together next white children begin got walk example ease paper group always music those both mark often letter until mile river car feet care second book carry took science eat room friend began idea fish mountain stop once base hear horse cut sure watch color face wood main enough plain girl usual young ready above ever red list though feel talk bird soon body dog family direct pose leave song measure door product black short numeral class wind question happen complete ship area half rock order fire south problem piece told knew pass since top whole king space heard best hour better true during hundred five remember step early hold west ground interest reach fast verb sing listen six table travel less morning ten simple several vowel toward war lay against pattern slow center love person money serve appear road map rain rule govern pull cold notice voice unit power town fine certain fly fall lead cry dark machine note wait plan figure star box noun field rest correct able pound done beauty drive stood contain front teach week final gave green oh quick develop ocean warm free minute strong special mind behind clear tail produce fact street inch multiply nothing course stay wheel full force blue object decide surface deep moon island foot system busy test record boat common gold possible plane stead dry wonder laugh thousand ago ran check game shape equate hot miss brought heat snow tire bring yes distant fill east paint language among grand ball yet wave drop heart am present heavy dance engine position arm wide sail material size vary settle speak weight general ice matter circle pair include divide syllable felt perhaps pick sudden count square reason length represent art subject region energy hunt probable bed brother egg ride cell believe fraction forest sit race window store summer train sleep prove lone leg exercise wall catch mount wish sky board joy winter sat written wild instrument kept glass grass cow job edge sign visit past soft fun bright gas weather month million bear finish happy hope flower clothe strange gone jump baby eight village meet root buy raise solve metal whether push seven paragraph third shall held hair describe cook floor either result burn hill safe cat century consider type law bit coast copy phrase silent tall sand soil roll temperature finger industry value fight lie beat excite natural view sense ear else quite broke case middle kill son lake moment scale loud spring observe child straight consonant nation dictionary milk speed method organ pay age section dress cloud surprise quiet stone tiny climb cool design poor lot experiment bottom key iron single stick flat twenty skin smile crease hole trade melody trip office receive row mouth exact symbol die least trouble shout except wrote seed tone join suggest clean break lady yard rise bad blow oil blood touch grew cent mix team wire cost lost brown wear garden equal sent choose fell fit flow fair bank collect save control decimal gentle woman captain practice separate difficult doctor please protect noon whose locate ring character insect caught period indicate radio spoke atom human history effect electric expect crop modern element hit student corner party supply bone rail imagine provide agree thus capital won't chair danger fruit rich thick soldier process operate guess necessary sharp wing create neighbor wash bat rather crowd corn compare poem string bell depend meat rub tube famous dollar stream fear sight thin triangle planet hurry chief colony clock mine tie enter major fresh search send yellow gun allow print dead spot desert suit current lift rose continue block chart hat sell success company subtract event particular deal swim term opposite wife shoe shoulder spread arrange camp invent cotton born determine quart nine truck noise level chance gather shop stretch throw shine property column molecule select wrong gray repeat require broad prepare salt nose plural anger claim continent oxygen sugar death pretty skill women season solution magnet silver thank branch match suffix especially fig afraid huge sister steel discuss forward similar guide experience score apple bought led pitch coat mass card band rope slip win dream evening condition feed tool total basic smell valley nor double seat arrive master track parent shore division sheet substance favor connect post spend chord fat glad original share station dad bread charge proper bar offer segment slave duck instant market degree populate chick dear enemy reply drink occur support speech nature range steam motion path liquid log meant quotient teeth shell neck "
unwanted_words = []
for word in str.split(" "):
    unwanted_words.append(word)

In [177]:
product_name = small_train["PRODUCT_ID"].tolist()

In [178]:
length = len(descriptions)

In [179]:
print(descriptions)

['always wooden bookmark minimalist quotes valentines day romance gift romantic quote heart lovers anniversary gift 100 real wood bookmark unique grain pattern uniquely designed wood bookmarks created natural ecofriendly wood wood used foresters follow sustainable yield harvesting methods size 7" x 175" x 364" 178 mm x 44 mm x 1 mm ultra thin flexible made usa uniquely designed wood bookmarks created natural ecofriendly wood 100 real wood bookmark unique grain pattern wood used foresters follow sustainable yield harvesting methods size 7" x 175" x 364" 178 mm x 44 mm x 1 mm ultra thin flexible made usa wood used produce bookmarks free chemicals upcycles byproducts logs foresters follow sustainable yield harvesting methods process make eco wood bookmarks ultra thin involved merely carving sawing slicing wood thinly forms thin layer wood cut log primary difference solid wood solid wood sawn log produces waste cutting thinly words processing log way maximizes added value obtained log prod

In [180]:
text_corpus = ""

for element in descriptions:
    text_corpus = text_corpus + str(element)

In [139]:
print(text_corpus)

always wooden bookmark minimalist quotes valentines day romance gift romantic quote heart lovers anniversary gift 100 real wood bookmark unique grain pattern uniquely designed wood bookmarks created natural ecofriendly wood wood used foresters follow sustainable yield harvesting methods size 7" x 175" x 364" 178 mm x 44 mm x 1 mm ultra thin flexible made usa uniquely designed wood bookmarks created natural ecofriendly wood 100 real wood bookmark unique grain pattern wood used foresters follow sustainable yield harvesting methods size 7" x 175" x 364" 178 mm x 44 mm x 1 mm ultra thin flexible made usa wood used produce bookmarks free chemicals upcycles byproducts logs foresters follow sustainable yield harvesting methods process make eco wood bookmarks ultra thin involved merely carving sawing slicing wood thinly forms thin layer wood cut log primary difference solid wood solid wood sawn log produces waste cutting thinly words processing log way maximizes added value obtained log produc

In [181]:
stop_words = set(stopwords.words('english'))
word_tokens = word_tokenize(text_corpus)
filtered_corpus = []
for w in word_tokens:
    if w not in stop_words:
        filtered_corpus.append(w)

In [182]:
filtered_corpus

['always',
 'wooden',
 'bookmark',
 'minimalist',
 'quotes',
 'valentines',
 'day',
 'romance',
 'gift',
 'romantic',
 'quote',
 'heart',
 'lovers',
 'anniversary',
 'gift',
 '100',
 'real',
 'wood',
 'bookmark',
 'unique',
 'grain',
 'pattern',
 'uniquely',
 'designed',
 'wood',
 'bookmarks',
 'created',
 'natural',
 'ecofriendly',
 'wood',
 'wood',
 'used',
 'foresters',
 'follow',
 'sustainable',
 'yield',
 'harvesting',
 'methods',
 'size',
 '7',
 "''",
 'x',
 '175',
 "''",
 'x',
 '364',
 "''",
 '178',
 'mm',
 'x',
 '44',
 'mm',
 'x',
 '1',
 'mm',
 'ultra',
 'thin',
 'flexible',
 'made',
 'usa',
 'uniquely',
 'designed',
 'wood',
 'bookmarks',
 'created',
 'natural',
 'ecofriendly',
 'wood',
 '100',
 'real',
 'wood',
 'bookmark',
 'unique',
 'grain',
 'pattern',
 'wood',
 'used',
 'foresters',
 'follow',
 'sustainable',
 'yield',
 'harvesting',
 'methods',
 'size',
 '7',
 "''",
 'x',
 '175',
 "''",
 'x',
 '364',
 "''",
 '178',
 'mm',
 'x',
 '44',
 'mm',
 'x',
 '1',
 'mm',
 'ultra',

In [183]:
frequency = collections.Counter(filtered_corpus)

In [184]:
frequency=(dict(frequency))

In [185]:
frequency

{'always': 129,
 'wooden': 179,
 'bookmark': 6,
 'minimalist': 14,
 'quotes': 25,
 'valentines': 13,
 'day': 503,
 'romance': 5,
 'gift': 944,
 'romantic': 26,
 'quote': 23,
 'heart': 61,
 'lovers': 25,
 'anniversary': 91,
 '100': 854,
 'real': 126,
 'wood': 387,
 'unique': 461,
 'grain': 38,
 'pattern': 320,
 'uniquely': 26,
 'designed': 685,
 'bookmarks': 13,
 'created': 53,
 'natural': 319,
 'ecofriendly': 108,
 'used': 689,
 'foresters': 3,
 'follow': 24,
 'sustainable': 17,
 'yield': 6,
 'harvesting': 3,
 'methods': 23,
 'size': 1902,
 '7': 195,
 "''": 2351,
 'x': 1664,
 '175': 13,
 '364': 4,
 '178': 2,
 'mm': 154,
 '44': 48,
 '1': 1293,
 'ultra': 146,
 'thin': 108,
 'flexible': 162,
 'made': 1897,
 'usa': 193,
 'produce': 32,
 'free': 563,
 'chemicals': 52,
 'upcycles': 1,
 'byproducts': 1,
 'logs': 1,
 'process': 128,
 'make': 770,
 'eco': 33,
 'involved': 6,
 'merely': 2,
 'carving': 6,
 'sawing': 1,
 'slicing': 3,
 'thinly': 3,
 'forms': 25,
 'layer': 152,
 'cut': 199,
 'log':

In [186]:
max(frequency)

'zzzzzzlast'

In [187]:
values=frequency.values()

In [188]:
sorted_x = sorted(frequency.items(), key=operator.itemgetter(-1))

In [212]:
unwanted_words

['',
 'the',
 'of',
 'to',
 'and',
 'a',
 'in',
 'is',
 'it',
 'you',
 'that',
 'he',
 'was',
 'for',
 'on',
 'are',
 'with',
 'as',
 'I',
 'his',
 'they',
 'be',
 'at',
 'one',
 'have',
 'this',
 'from',
 'or',
 'had',
 'by',
 'not',
 'word',
 'but',
 'what',
 'some',
 'we',
 'can',
 'out',
 'other',
 'were',
 'all',
 'there',
 'when',
 'up',
 'use',
 'your',
 'how',
 'said',
 'an',
 'each',
 'she',
 'which',
 'do',
 'their',
 'time',
 'if',
 'will',
 'way',
 'about',
 'many',
 'then',
 'them',
 'write',
 'would',
 'like',
 'so',
 'these',
 'her',
 'long',
 'make',
 'thing',
 'see',
 'him',
 'two',
 'has',
 'look',
 'more',
 'day',
 'could',
 'go',
 'come',
 'did',
 'number',
 'sound',
 'no',
 'most',
 'people',
 'my',
 'over',
 'know',
 'water',
 'than',
 'call',
 'first',
 'who',
 'may',
 'down',
 'side',
 'been',
 'now',
 'find',
 'any',
 'new',
 'work',
 'part',
 'take',
 'get',
 'place',
 'made',
 'live',
 'where',
 'after',
 'back',
 'little',
 'only',
 'round',
 'man',
 'year',

In [189]:
sorted_x

[('upcycles', 1),
 ('byproducts', 1),
 ('logs', 1),
 ('sawing', 1),
 ('nonhumid', 1),
 ('nestled', 1),
 ('pageskinda', 1),
 ('guyfagna', 1),
 ('fcckq30choclateyxl', 1),
 ('alineotherlands', 1),
 ('journeys', 1),
 ('extinct', 1),
 ('ecosystemstoothless', 1),
 ('tlpgca3931', 1),
 ('shinersaison', 1),
 ('mes', 1),
 ('matchs', 1),
 ('comptitions', 1),
 ('entranements', 1),
 ('karatka', 1),
 ('garon', 1),
 ('fille', 1),
 ('enfant', 1),
 ('ado', 1),
 ('formatkayra', 1),
 ('053m', 1),
 ('httpswwwamazonindpb07kwzwq12', 1),
 ('393', 1),
 ('redecoration', 1),
 ('cofriendly', 1),
 ('fireretardant', 1),
 ('strippable', 1),
 ('elongation', 1),
 ('wwwamazonindpb07kwzwq12', 1),
 ('problemleague', 1),
 ('fountaincrufix', 1),
 ('thankenamor', 1),
 ('a042', 1),
 ('fab', 1),
 ('flexigrip', 1),
 ('noshow', 1),
 ('hooked', 1),
 ('monthsdeadly', 1),
 ('murdernkjv', 1),
 ('floweradvancedestore', 1),
 ('dvancedestore', 1),
 ('advancedestore', 1),
 ('seedsfranco', 1),
 ('hasbro', 1),
 ('ponies', 1),
 ('pinkie'

In [190]:
sorted_x=list(sorted_x)[-1000:]

[('separately', 71),
 ('charge', 71),
 ('la', 71),
 ('guaranteed', 71),
 ('colours', 71),
 ('finest', 72),
 ('unisex', 72),
 ('23', 72),
 ('funny', 72),
 ('shade', 72),
 ('along', 72),
 ('noise', 72),
 ('meter', 72),
 ('slight', 73),
 ('evening', 73),
 ('wardrobe', 73),
 ('condition', 73),
 ('conditions', 73),
 ('packed', 73),
 ('leggings', 73),
 ('eye', 73),
 ('dimension', 73),
 ('halloween', 73),
 ('save', 73),
 ('less', 74),
 ('wallpaper', 74),
 ('self', 74),
 ('compatibility', 74),
 ('price', 74),
 ('together', 74),
 ('measure', 74),
 ('months', 74),
 ('universal', 74),
 ('contrast', 74),
 ('tshirts', 74),
 ('notebook', 74),
 ('return', 74),
 ('electric', 74),
 ('change', 74),
 ('environment', 74),
 ('serving', 74),
 ('comfy', 75),
 ('personal', 75),
 ('beautifully', 75),
 ('pendant', 75),
 ('inks', 75),
 ('images', 75),
 ('micro', 75),
 ('ease', 75),
 ('kickstand', 75),
 ('5g', 75),
 ('screw', 75),
 ('32', 75),
 ('clock', 75),
 ('know', 76),
 ('tab', 76),
 ('builtin', 76),
 ('diam

In [102]:
small_train = pd.read_csv("dataset/small_train.csv").fillna(" ")

In [103]:
small_train = train.iloc[:40000]

In [104]:
small_train

PRODUCT_ID                                              TITLE  \
0         1925202  ArtzFolio Tulip Flowers Blackout Curtain for D...   
1         2673191  Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2         2765088  PRIKNIK Horn Red Electric Air Horn Compressor ...   
3         1594019  ALISHAH Women's Cotton Ankle Length Leggings C...   
4          283658  The United Empire Loyalists: A Chronicle of th...   
...           ...                                                ...   
39995     1721150  INVENTO 1PCS 0.28" LED Voltmeter Ammeter, Red ...   
39996     2213385  Kawn Enamelled Metal Crystal Easter Floral Gol...   
39997      828894      Halex Beach Toss Jai Lai Botas (Purple/Green)   
39998      549617  Handbook of Enemy Ammunition: War Office Pamph...   
39999      953649  Top of The World NCAA Triple Threat Wool Adjus...   

                                           BULLET_POINTS  \
0      [LUXURIOUS & APPEALING: Beautiful custom-made ...   
1      [Harry Potter Hedwig Pyjamas (6-16 Yrs),100% c...   
2      [Loud Dual Tone Trumpet Horn, Compatible With ...   
3      [Made By 95%cotton and 5% Lycra which gives yo...   
4                                                    NaN   
...                                                  ...   
39995  [0.28" inch LED digital display with Red & Blu...   
39996  [Vintage exquisite flower green egg jewelry bo...   
39997  [Two molded brightly colored Jai alai Botas.,O...   
39998                                                NaN   
39999  [Wool blend slight structure,College team colo...   

                                             DESCRIPTION  PRODUCT_TYPE_ID  \
0                                                    NaN             1650   
1                                                    NaN             2755   
2      Specifications: Color: Red, Material: Aluminiu...             7537   
3      AISHAH Women's Lycra Cotton Ankel Leggings. Br...             2996   
4                                                    NaN             6112   
...                                                  ...              ...   
39995                                                NaN            10540   
39996  <p><b>Description:</b></p><p>Vintage exquisite...             3329   
39997                    Includes 2 catchers and 1 ball.              976   
39998                                                NaN             6111   
39999                                                NaN                0   

       PRODUCT_LENGTH  
0         2125.980000  
1          393.700000  
2          748.031495  
3          787.401574  
4          598.424000  
...               ...  
39995      196.850000  
39996      433.070866  
39997      430.000000  
39998      614.000000  
39999      800.000000  

[40000 rows x 6 columns]

In [98]:
#small_train.drop("TEXT")

In [99]:
small_train["TEXT"] = small_train["TITLE"][:]+small_train["BULLET_POINTS"][:]+ small_train["DESCRIPTION"][:]

/var/folders/ck/gs22xnt513x04n1m13hg3w6h0000gr/T/ipykernel_1680/2161983442.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  small_train["TEXT"] = small_train["TITLE"][:]+small_train["BULLET_POINTS"][:]+ small_train["DESCRIPTION"][:]


In [100]:
small_train["TEXT"]

0                                                      NaN
1                                                      NaN
2        PRIKNIK Horn Red Electric Air Horn Compressor ...
3        ALISHAH Women's Cotton Ankle Length Leggings C...
4                                                      NaN
                               ...                        
39995                                                  NaN
39996    Kawn Enamelled Metal Crystal Easter Floral Gol...
39997    Halex Beach Toss Jai Lai Botas (Purple/Green)[...
39998                                                  NaN
39999                                                  NaN
Name: TEXT, Length: 40000, dtype: object

In [35]:
title = pd.DataFrame(small_train["TITLE"])

In [36]:
title


TITLE
0      ArtzFolio Tulip Flowers Blackout Curtain for D...
1      Marks & Spencer Girls' Pyjama Sets T86_2561C_N...
2      PRIKNIK Horn Red Electric Air Horn Compressor ...
3      ALISHAH Women's Cotton Ankle Length Leggings C...
4      The United Empire Loyalists: A Chronicle of th...
...                                                  ...
39995  INVENTO 1PCS 0.28" LED Voltmeter Ammeter, Red ...
39996  Kawn Enamelled Metal Crystal Easter Floral Gol...
39997      Halex Beach Toss Jai Lai Botas (Purple/Green)
39998  Handbook of Enemy Ammunition: War Office Pamph...
39999  Top of The World NCAA Triple Threat Wool Adjus...

[40000 rows x 1 columns]

In [80]:
import spacy
nlp = spacy.load("en_core_web_sm")

def get_ents(doc):
    if doc.ents:
        for ent in doc.ents:
            #return(f"ent.text -> {ent.text}, ent.start-> {ent.start}, ent.end -> {ent.end}, ent.start_char-> {ent.start_char}, ent.end_char ->{ent.end_char}, ent.label_ ->{ent.label_}")
            return(f"ent.text -> {ent.text}, ent.label_ ->{ent.label_}")
    else:
        return("No entities found")




In [81]:
title_list = title["TITLE"].to_list()


In [82]:

#title = title.drop("ents",axis = "columns")


In [83]:
title_list

['ArtzFolio Tulip Flowers Blackout Curtain for Door, Window & Room | Eyelets & Tie Back | Canvas Fabric | Width 4.5feet (54inch) Height 5 feet (60 inch); Set of 2 PCS',
 "Marks & Spencer Girls' Pyjama Sets T86_2561C_Navy Mix_9-10Y",
 'PRIKNIK Horn Red Electric Air Horn Compressor Interior Dual Tone Trumpet Loud Compatible with SX4',
 "ALISHAH Women's Cotton Ankle Length Leggings Combo of 2, Plus 12 Colors_L",
 'The United Empire Loyalists: A Chronicle of the Great Migration',
 'HINS Metal Bucket Shape Plant Pot for Indoor & Outdoor Gardening (Red, Medium) Plant Stands for Indoor Balcony I Plant Bench I Plant Stands I Pot Stand Single I Potted Plant Stand I Big Pots I Metal',
 'Ungifted: My Life and Journey',
 'Delavala Self Adhesive Kitchen Backsplash Wallpaper, Oil Proof Aluminum Foil Kitchen Sticker (Sliver 5(Mtr))',
 "PUMA Cali Sport Clean Women's Sneakers White Leather (37540701)",
 'Hexwell Essential oil for Home Fragrance Oil Aroma Diffuser oil Set of 2 Rajnigandha Oil & TeaTree 

In [85]:
ents = []

for element in title_list :
    
    doc = nlp(element)
    ents.append(str(get_ents(doc)))


In [86]:
ents

['ent.text -> Canvas Fabric, ent.label_ ->PRODUCT',
 'ent.text -> Marks & Spencer, ent.label_ ->ORG',
 'ent.text -> PRIKNIK Horn Red Electric Air Horn Compressor, ent.label_ ->ORG',
 'ent.text -> 2, ent.label_ ->CARDINAL',
 'ent.text -> The United Empire Loyalists: A Chronicle of the Great Migration, ent.label_ ->ORG',
 'ent.text -> HINS Metal Bucket Shape Plant Pot for Indoor & Outdoor Gardening (Red, Medium) Plant Stands for Indoor Balcony, ent.label_ ->ORG',
 'ent.text -> Journey, ent.label_ ->PERSON',
 'ent.text -> Delavala Self Adhesive, ent.label_ ->PERSON',
 "ent.text -> PUMA Cali Sport Clean Women's, ent.label_ ->PERSON",
 'ent.text -> Hexwell Essential, ent.label_ ->ORG',
 'No entities found',
 'ent.text -> La Mure / Valbonnais, ent.label_ ->ORG',
 "ent.text -> J'ecris, ent.label_ ->NORP",
 'ent.text -> Mediterranean, ent.label_ ->LOC',
 'ent.text -> Water Bottle, ent.label_ ->PERSON',
 'ent.text -> Stone & Beam Fan, ent.label_ ->ORG',
 'No entities found',
 'ent.text -> Steel

In [87]:
title["ents"] = ents

In [88]:
title

TITLE  \
0      ArtzFolio Tulip Flowers Blackout Curtain for D...   
1      Marks & Spencer Girls' Pyjama Sets T86_2561C_N...   
2      PRIKNIK Horn Red Electric Air Horn Compressor ...   
3      ALISHAH Women's Cotton Ankle Length Leggings C...   
4      The United Empire Loyalists: A Chronicle of th...   
...                                                  ...   
39995  INVENTO 1PCS 0.28" LED Voltmeter Ammeter, Red ...   
39996  Kawn Enamelled Metal Crystal Easter Floral Gol...   
39997      Halex Beach Toss Jai Lai Botas (Purple/Green)   
39998  Handbook of Enemy Ammunition: War Office Pamph...   
39999  Top of The World NCAA Triple Threat Wool Adjus...   

                                                    ents  
0        ent.text -> Canvas Fabric, ent.label_ ->PRODUCT  
1          ent.text -> Marks & Spencer, ent.label_ ->ORG  
2      ent.text -> PRIKNIK Horn Red Electric Air Horn...  
3                   ent.text -> 2, ent.label_ ->CARDINAL  
4      ent.text -> The United Empire Loyalists: A Chr...  
...                                                  ...  
39995  ent.text -> Red and Blue Digital Multimeter Di...  
39996              ent.text -> Kawn, ent.label_ ->PERSON  
39997       ent.text -> Halex Beach, ent.label_ ->PERSON  
39998              ent.text -> 10, ent.label_ ->CARDINAL  
39999  ent.text -> The World NCAA Triple Threat Wool ...  

[40000 rows x 2 columns]

In [90]:
title.to_csv("entites_from_title.csv")